In [1]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [2]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [3]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/PhysicalProgressReport/YearWiseHouseCompletionReport.aspx?"
params = {
    'params': 0
}
for key, value in params.items():
    url = url + "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [4]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddlFinYear'
scheme_select_name = 'ctl00$ContentPlaceHolder1$ddlScheme'
state_select_name = 'ctl00$ContentPlaceHolder1$ddlState'
district_select_name = 'ctl00$ContentPlaceHolder1$ddlDistrict'
block_select_name = 'ctl00$ContentPlaceHolder1$ddlBlock'
submit_button_name = 'ctl00$ContentPlaceHolder1$btnSubmit'
content_table_pane = 'ContentPlaceHolder1_gvDataPanelItem'
content_table_head_id = 'ContentPlaceHolder1_gvDataCopy'
content_table_id = 'ContentPlaceHolder1_gvData'

In [5]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

#Check Submit button
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )

#Check table
def delete_submit():
    driver.execute_script("return document.getElementsByName('" + submit_button_name + "')[0].remove()")
def check_submit():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, submit_button_name ) ) )    
    
#Check submit button
def delete_content():
    driver.execute_script("return document.getElementsByClassName('col-lg-10')[0].remove()")
def check_error():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.ID, "ContentPlaceHolder1_lbl_data_msg" ) ) )
    

In [6]:
def get_total_houselist():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
    WebDriverWait(driver, 2).until(element_present)
    #Once Loaded Create DataFrame from Table
    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
    df = pd.read_html(html_table, skiprows=0, header=0)[0]
    df = df[1:-1]        
    total_houses_completed = list(df[df.columns[-1]])
    return total_houses_completed

In [7]:
#Start Chrome
driver.get(url)

#Year Selection
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[4:5]
for year in yearlist:    
    print("--Scrapping data for Year: ", year['text'])
    year_query = ".//option[@value='" + year['value'] + "']"
    delete_submit()
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    check_submit()
    
    #DataStore
    df_list = []
    
    #Scheme Selection
    schemelist = build_list(scheme_select_name)[1:]
    for scheme in schemelist:
        print("--//--Scrapping data for scheme: ", scheme['text'])
        scheme_query = ".//option[@value='" + scheme['value'] + "']"
        delete_submit()
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, scheme_select_name))
        )
        element.find_element_by_xpath(scheme_query).click()
        check_submit()
        
        # Delete Content
        delete_content()        
        #Submit button
        element = WebDriverWait(driver, 10).until(
            EC.element_to_be_clickable((By.NAME, submit_button_name))
        )
        element.click()
        
        #Load Filter List
        state_total_houses_completed = get_total_houselist();
        
        #state Selection
        statelist = build_list(state_select_name)
        for stateindex, state in enumerate(statelist):
            print("--//--//--Scrapping data for state: ", state['text'])
            if state_total_houses_completed[int(stateindex)] > 0:
                state_query = ".//option[@value='" + state['value'] + "']"
                delete_submit()
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, state_select_name))
                )
                element.find_element_by_xpath(state_query).click()
                check_submit()
                
                # Delete Content
                delete_content()        
                #Submit button
                element = WebDriverWait(driver, 10).until(
                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                )
                element.click()

                #Load Filter List
                district_total_houses_completed = get_total_houselist();
         
                #district Selection
                districtlist = build_list(district_select_name)
                for districtindex, district in enumerate(districtlist):
                    print("--//--//--//--Scrapping data for district: ", district['text'])
                    if district_total_houses_completed[int(districtindex)] > 0:
                        district_query = ".//option[@value='" + district['value'] + "']"
                        delete_submit()
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, district_select_name))
                        )
                        element.find_element_by_xpath(district_query).click()
                        check_submit()
                        
                        # Delete Content
                        delete_content()        
                        #Submit button
                        element = WebDriverWait(driver, 10).until(
                            EC.element_to_be_clickable((By.NAME, submit_button_name))
                        )
                        element.click()

                        #Load Filter List
                        block_total_houses_completed = get_total_houselist();

                        #block Selection
                        blocklist = build_list(block_select_name)
                        for blockindex, block in enumerate(blocklist):
                            print("--//--//--//--//--Scrapping data for block: ", block['text'])
                            if block_total_houses_completed[int(blockindex)] > 0:
                                block_query = ".//option[@value='" + block['value'] + "']"
                                delete_submit()
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, block_select_name))
                                )
                                element.find_element_by_xpath(block_query).click()
                                check_submit()

                                # Delete Content
                                delete_content()

                                #Submit button
                                element = WebDriverWait(driver, 10).until(
                                    EC.element_to_be_clickable((By.NAME, submit_button_name))
                                )
                                element.click()

                                try:
                                    #Wait for Table to Load fully
                                    element_present = EC.presence_of_element_located((By.ID, content_table_id))            
                                    WebDriverWait(driver, 2).until(element_present)

                                    #Once Loaded Create DataFrame from Table
                                    #html_head = driver.find_element_by_id(content_table_head_id).get_attribute('outerHTML')
                                    #df = pd.read_html(html_head, skiprows=0)[0]
                                    #table_head = list(df.values[0])
                                    html_table = driver.find_element_by_id(content_table_id).get_attribute('outerHTML')
                                    df = pd.read_html(html_table, skiprows=0, header=0)[0]
                                    df = df[1:-1]
                                    #df.columns = table_head
                                    df['Financial Year'] = year['text']
                                    df['Scheme'] = scheme['text']
                                    df['State Name'] = state['text']
                                    df['District Name'] = district['text']
                                    df['Block Name'] = block['text']
                                    df_list.append(df)
                                except Exception as e:
                                    print("Error while table data |", e)


    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df = df.reset_index().drop(columns=['index', '#SNo'])
    df['#SNo'] = df.index + 1
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

--Scrapping data for Year:  2014-2015
--//--Scrapping data for scheme:  ALL CENTRAL SCHEMES
--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--//--Scrapping data for district:  ANJAW
--//--//--//--Scrapping data for district:  CHANGLANG
--//--//--//--Scrapping data for district:  EAST KAMENG
--//--//--//--Scrapping data for district:  EAST SIANG
--//--//--//--Scrapping data for district:  KRA-DAADI
--//--//--//--//--Scrapping data for block:  CHAMBANG
--//--//--//--//--Scrapping data for block:  GANGTE
--//--//--//--//--Scrapping data for block:  PALIN
--//--//--//--//--Scrapping data for block:  PIP SORANG
--//--//--//--//--Scrapping data for block:  TALI
--//--//--//--//--Scrapping data for block:  YANGTE
--//--//--//--Scrapping data for district:  KURUNG KUMEY
--//--//--//--Scrapping data for district:  LOHIT
--//--//--//--Scrapping data for district:  LONGDING
--//--//--//--Scrapping data for district:  LOWER DIBANG VALLEY
--//--//--//--Scrapping data for district:  L

--//--//--//--//--Scrapping data for block:  JORHAT
--//--//--//--//--Scrapping data for block:  JORHAT CENTRAL
--//--//--//--//--Scrapping data for block:  JORHAT EAST
--//--//--//--//--Scrapping data for block:  KALIAPANI
--//--//--//--//--Scrapping data for block:  MAJULI
--//--//--//--//--Scrapping data for block:  NORTH WEST JORHAT
--//--//--//--//--Scrapping data for block:  TITABOR
--//--//--//--//--Scrapping data for block:  UJANI MAJULI
--//--//--//--Scrapping data for district:  KAMRUP
--//--//--//--//--Scrapping data for block:  BEZERA
--//--//--//--//--Scrapping data for block:  BIHDIA JAJIKONA
--//--//--//--//--Scrapping data for block:  BOKO
--//--//--//--//--Scrapping data for block:  BONGAON
--//--//--//--//--Scrapping data for block:  CHAMARIA
--//--//--//--//--Scrapping data for block:  CHAYANI BARDUAR (PART)
--//--//--//--//--Scrapping data for block:  CHAYGAON
--//--//--//--//--Scrapping data for block:  GOROIMARI
--//--//--//--//--Scrapping data for block:  HAJO
--

--//--//--//--//--Scrapping data for block:  KHOIRABARI
--//--//--//--//--Scrapping data for block:  MAZBAT
--//--//--//--//--Scrapping data for block:  PASCHIM-MANGALDAI
--//--//--//--//--Scrapping data for block:  PUB-MANGALDAI
--//--//--//--//--Scrapping data for block:  ROWTA
--//--//--//--//--Scrapping data for block:  UDALGURI
--//--//--Scrapping data for state:  BIHAR
--//--//--//--Scrapping data for district:  ARARIA
--//--//--//--//--Scrapping data for block:  ARARIA
--//--//--//--//--Scrapping data for block:  BHARGAMA
--//--//--//--//--Scrapping data for block:  FORBESGANJ
--//--//--//--//--Scrapping data for block:  JOKIHAT
--//--//--//--//--Scrapping data for block:  KURSAKANTA
--//--//--//--//--Scrapping data for block:  NARPATGANJ
--//--//--//--//--Scrapping data for block:  PALASI
--//--//--//--//--Scrapping data for block:  RANIGANJ
--//--//--//--//--Scrapping data for block:  SIKTY
--//--//--//--Scrapping data for district:  ARWAL
--//--//--//--//--Scrapping data for 

--//--//--//--//--Scrapping data for block:  WAZIRGANG
--//--//--//--Scrapping data for district:  GOPALGANJ
--//--//--//--//--Scrapping data for block:  BAIKUNTHPUR
--//--//--//--//--Scrapping data for block:  BARAULI
--//--//--//--//--Scrapping data for block:  BHOREY
--//--//--//--//--Scrapping data for block:  BIJAIPUR
--//--//--//--//--Scrapping data for block:  GOPALGANJ
--//--//--//--//--Scrapping data for block:  HATHUA
--//--//--//--//--Scrapping data for block:  KATAIYA
--//--//--//--//--Scrapping data for block:  KUCHAIKOTE
--//--//--//--//--Scrapping data for block:  MANJHA
--//--//--//--//--Scrapping data for block:  PANCHDEORI
--//--//--//--//--Scrapping data for block:  PHULWARIYA
--//--//--//--//--Scrapping data for block:  SIDHWALIA
--//--//--//--//--Scrapping data for block:  THAWE
--//--//--//--//--Scrapping data for block:  UCHKAGAON
--//--//--//--Scrapping data for district:  JAMUI
--//--//--//--//--Scrapping data for block:  BARHAT
--//--//--//--//--Scrapping data

--//--//--//--//--Scrapping data for block:  ASTHAWAN BLOCK
--//--//--//--//--Scrapping data for block:  BEN
--//--//--//--//--Scrapping data for block:  BIHARSARIF
--//--//--//--//--Scrapping data for block:  BIND BLOCK
--//--//--//--//--Scrapping data for block:  CHANDI BLOCK
--//--//--//--//--Scrapping data for block:  EKANGARSARAI
--//--//--//--//--Scrapping data for block:  GIRIYAK
--//--//--//--//--Scrapping data for block:  HARNAUT BLOCK
--//--//--//--//--Scrapping data for block:  HILSA
--//--//--//--//--Scrapping data for block:  ISLAMPUR  BLOCK
--//--//--//--//--Scrapping data for block:  KARAIPARSURAI
--//--//--//--//--Scrapping data for block:  KATRISARAI
--//--//--//--//--Scrapping data for block:  NAGARNAUSA
--//--//--//--//--Scrapping data for block:  NOORSARAI
--//--//--//--//--Scrapping data for block:  PARWALPUR
--//--//--//--//--Scrapping data for block:  RAHUI BLOCK
--//--//--//--//--Scrapping data for block:  RAJGIR BLOCK
--//--//--//--//--Scrapping data for block:

...

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--//--Scrapping data for district:  BILASPUR
--//--//--//--Scrapping data for district:  CHAMBA
--//--//--//--//--Scrapping data for block:  BHARMOUR
--//--//--//--//--Scrapping data for block:  BHATTIYAT
--//--//--//--//--Scrapping data for block:  CHAMBA
--//--//--//--//--Scrapping data for block:  MEHLA
--//--//--//--//--Scrapping data for block:  PANGI
--//--//--//--//--Scrapping data for block:  SALOONI
--//--//--//--//--Scrapping data for block:  TISSA
--//--//--//--Scrapping data for district:  HAMIRPUR
--//--//--//--//--Scrapping data for block:  BAMSON
--//--//--//--//--Scrapping data for block:  BHO

--//--//--//--Scrapping data for district:  DHALAI
--//--//--//--//--Scrapping data for block:  AMBASSA
--//--//--//--//--Scrapping data for block:  CHAWMANU
--//--//--//--//--Scrapping data for block:  DUMBURNAGAR
--//--//--//--//--Scrapping data for block:  DURGACHOWMUHANI
--//--//--//--//--Scrapping data for block:  GANGANAGAR
--//--//--//--//--Scrapping data for block:  MANU
--//--//--//--//--Scrapping data for block:  RAISHYABARI
--//--//--//--//--Scrapping data for block:  SALEMA
--//--//--//--Scrapping data for district:  GOMATI
--//--//--//--//--Scrapping data for block:  AMARPUR
--//--//--//--//--Scrapping data for block:  KAKRABAN
--//--//--//--//--Scrapping data for block:  KARBOOK
--//--//--//--//--Scrapping data for block:  KILLA
--//--//--//--//--Scrapping data for block:  MATABARI
--//--//--//--//--Scrapping data for block:  OMPI
--//--//--//--//--Scrapping data for block:  SHILACHARI
--//--//--//--//--Scrapping data for block:  TEPANIA
--//--//--//--Scrapping data for d

--//--//--//--//--Scrapping data for block:  BRAHMPUR
--//--//--//--//--Scrapping data for block:  BUXAR
--//--//--//--//--Scrapping data for block:  CHAKKI
--//--//--//--//--Scrapping data for block:  CHAUSA
--//--//--//--//--Scrapping data for block:  CHOUGAI
--//--//--//--//--Scrapping data for block:  DUMRAON
--//--//--//--//--Scrapping data for block:  ITARHI
--//--//--//--//--Scrapping data for block:  KESATH
--//--//--//--//--Scrapping data for block:  NAWANAGAR
--//--//--//--//--Scrapping data for block:  RAJPUR
--//--//--//--//--Scrapping data for block:  SIMRI
--//--//--//--Scrapping data for district:  DARBHANGA
--//--//--//--Scrapping data for district:  GAYA
--//--//--//--Scrapping data for district:  GOPALGANJ
--//--//--//--Scrapping data for district:  JAMUI
--//--//--//--Scrapping data for district:  JEHANABAD
--//--//--//--Scrapping data for district:  KAIMUR (BHABUA)
--//--//--//--Scrapping data for district:  KATIHAR
--//--//--//--Scrapping data for district:  KHAGAR

--//--//--//--//--Scrapping data for block:  KIPHIRE
--//--//--//--//--Scrapping data for block:  LONGMATRA
--//--//--//--//--Scrapping data for block:  PUNGRO
--//--//--//--//--Scrapping data for block:  SITIMI
--//--//--//--Scrapping data for district:  KOHIMA
--//--//--//--//--Scrapping data for block:  BOTSA
--//--//--//--//--Scrapping data for block:  CHEIPHOBOZOU
--//--//--//--//--Scrapping data for block:  CHUNLIKHA
--//--//--//--//--Scrapping data for block:  JAKHAMA
--//--//--//--//--Scrapping data for block:  KOHIMA
--//--//--//--//--Scrapping data for block:  SECHU-ZUBZA
--//--//--//--//--Scrapping data for block:  TSEMINYU
--//--//--//--Scrapping data for district:  LONGLENG
--//--//--//--//--Scrapping data for block:  LONGLENG
--//--//--//--//--Scrapping data for block:  SAKSHI
--//--//--//--//--Scrapping data for block:  TAMLU
--//--//--//--Scrapping data for district:  MOKOKCHUNG
--//--//--//--//--Scrapping data for block:  CHANGTONGYA
--//--//--//--//--Scrapping data fo

--//--//--Scrapping data for state:  ARUNACHAL PRADESH
--//--//--Scrapping data for state:  ASSAM
--//--//--Scrapping data for state:  BIHAR
--//--//--Scrapping data for state:  CHHATTISGARH
--//--//--Scrapping data for state:  GOA
--//--//--Scrapping data for state:  GUJARAT
--//--//--Scrapping data for state:  HARYANA
--//--//--Scrapping data for state:  HIMACHAL PRADESH
--//--//--Scrapping data for state:  JAMMU AND KASHMIR
--//--//--Scrapping data for state:  JHARKHAND
--//--//--Scrapping data for state:  KERALA
--//--//--Scrapping data for state:  MADHYA PRADESH
--//--//--Scrapping data for state:  MAHARASHTRA
--//--//--Scrapping data for state:  MANIPUR
--//--//--Scrapping data for state:  MEGHALAYA
--//--//--Scrapping data for state:  MIZORAM
--//--//--Scrapping data for state:  NAGALAND
--//--//--Scrapping data for state:  ODISHA
--//--//--//--Scrapping data for district:  ANGUL
--//--//--//--Scrapping data for district:  BALESHWAR
--//--//--//--//--Scrapping data for block:  B

In [13]:
df = pd.concat(df_list)

In [14]:
df

#SNo     Panchayat Name  Houses completed for prior to 2009-2010  \
1    1.0    Amla Singh Wala                                        0   
2    2.0            Bahmnia                                        0   
3    3.0          Bhadalwad                                        0   
4    4.0              Bihla                                        0   
5    5.0        Bihla Khurd                                        0   
6    6.0          Chananwal                                        0   
7    7.0             Chhapa                                        0   
8    8.0    Chhiniwal Kalan                                        0   
9    9.0    Chhiniwal Khurd                                        0   
10  10.0     Chuhanke Kalan                                        0   
11  11.0     Chuhanke Khurd                                        0   
12  12.0             Dhaner                                        0   
13  13.0             Diwana                                        0   
14  14.0            Gagewal                                        0   
15  15.0           Gangohar                                        0   
16  16.0              Gehal                                        0   
17  17.0         Hardaspura                                        0   
18  18.0        Kalal Majra                                        0   
19  19.0             Kalala                                        0   
20  20.0             Khiali                                        0   
21  21.0  Kirpal Singh Wala                                        0   
22  22.0              Kurar                                        0   
23  23.0              Kutba                                        0   
24  24.0            Lohgarh                                        0   
25  25.0        Mehal Kalan                                        0   
26  26.0   Mehal Kalan Sode                                        0   
27  27.0        Mehal Khurd                                        0   
28  28.0               Moom                                        0   
29  29.0  Naraingarh Sohian                                        0   
30  30.0         Nihaluwala                                        0   
..   ...                ...                                      ...   
11  11.0           Chapatla                                        0   
12  12.0         Chinnakara                                        0   
13  13.0           Gajarkot                                        0   
14  14.0           Haligera                                        0   
15  15.0          Hattikuni                                        0   
16  16.0           Honageri                                        0   
17  17.0            Jaigram                                        0   
18  18.0           Kadechur                                        0   
19  19.0           Kakalwar                                        0   
20  20.0       Kalebelgunda                                        0   
21  21.0           Kandkuru                                        0   
22  22.0         Killankera                                        0   
23  23.0             Konkal                                        0   
24  24.0            Kouluru                                        0   
25  25.0             Madwar                                        0   
26  26.0             Malhar                                        0   
27  27.0           Minaspur                                        0   
28  28.0           Motnalli                                        0   
29  29.0             Mudnal                                        0   
30  30.0           Mundargi                                        0   
31  31.0            Paspool                                        0   
32  32.0             Putpak                                        0   
33  33.0         Ramsamudra                                        0   
34  34.0           Saidapur                 

In [15]:
df = pd.concat(df_list)
df = df.reset_index().drop(columns=['index', '#SNo'])
df['#SNo'] = df.index + 1
#Save Scrapped File
df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)